# Show difference
In this notebook we provide visualization of extracted graphs and also visualization of differences in this graph. 

In [1]:
import osmnx as ox
import networkx as nx
import folium

In the code below please provide graphs from the same city from different timestamps.

In [2]:
first_path = "graphml_files/wroclaw_2012"
first_graph = ox.io.load_graphml(first_path)


In [3]:
#first_path = "graphml_files/europe_italy_milano_2012"
#second_path = "graphml_files/europe_italy_milano_2022"

first_path = "graphml_files/wroclaw_2012"
second_path = "graphml_files/wroclaw_2022"

In [4]:
first_graph = ox.io.load_graphml(first_path)
second_graph = ox.io.load_graphml(second_path)

In [5]:
def difference(first, second):
    dif = nx.create_empty_copy(second)
    dif_cycle = nx.create_empty_copy(second)
    dif.name = f"Difference of {first.name} and {second.name} without cycleway"
    dif_cycle.name = f"Difference of {first.name} and {second.name} with only cycleway"
    
    dif_nodes = set(second) - set(first)
    if len(dif_nodes) == 0:
        print("There are no new nodes")
    
    dif_edges = set(second.edges()) - set(first.edges())
    if len(dif_nodes) == 0:
        print("There are no new edges")
        
    for edge in set(second.edges()):
        for x in second.edges([edge[0], edge[1]], data=True):
            save=True
            x_values = x[2]
            x_values.pop('osmid', None) 
            x_values.pop('name', None)
            vis_data_x = dict(years=[first.name, second.name], data={})
            for y in first.edges([edge[0], edge[1]], data=True):
                y_values = y[2]
                #print(y_values)
                y_values.pop('osmid', None) 
                y_values.pop('name', None)
                
                if x_values == y_values:
                    save=False
                
            if save:
                if x[2]['highway'] == 'cycleway':
                    #print(x[2])
                    #raise Exception
                    dif_cycle.add_edges_from([(x[0], x[1], x[2])])
                else:
                    x[2]['data'] = {'year':[2012, 2022] ,'data':{'highway':['path', 'residential'], 'oneway':[False, False], 'lanes':[0,1]}}
                    #print(x[2])

                    #raise Exception

                    dif.add_edges_from([(x[0], x[1], x[2])])
        
    return dif, dif_cycle

In [6]:
dif_graph, dif_graph_cycle = difference(first_graph, second_graph)

There are no new nodes
There are no new edges


In [7]:
dif_graph

In [8]:
print(f"Diff graph {dif_graph.name}")
ox.plot_graph_folium(dif_graph, popup_attribute="data") #speed, name, maxspeed, oneway, length

Diff graph Difference of wroclaw_2012 and wroclaw_2022 without cycleway


In [9]:
print(f"Diff graph with cycle ways{dif_graph_cycle.name}")
ox.plot_graph_folium(dif_graph_cycle, popup_attribute="highway") #speed, name, maxspeed, oneway, length

Diff graph with cycle waysDifference of wroclaw_2012 and wroclaw_2022 with only cycleway


ValueError: graph contains no edges

In [ ]:
print(f"First graph {first_graph.name}")
#ox.plot_graph(first_graph)
ox.plot_graph_folium(first_graph)

In [ ]:
print(f"Second graph {second_graph.name}")
ox.plot_graph_folium(second_graph)

In [ ]:
ox.plot_graph_folium(first_graph)